In [100]:
import numpy as np
import re
import pandas as pd

In [116]:
test_data1 = pd.read_csv('./data/last_really_data.csv',encoding='utf-8')
navidata = pd.read_csv('./hsnavidata/hs01.csv',encoding='utf-8',names = ['HSCODE','NM_KO','NM_EN'])
#test_data1.drop(['Unnamed: 0'],axis = 1, inplace = True)

In [117]:
#HSCODE 숫자만
dictionary = {'\n':'', '\t':'','-':''}
navidata.replace(dictionary,regex=True, inplace = True)
navidata['HSCODE'] = navidata['HSCODE'].str.replace('.','')
navidata['HSCODE'] = navidata['HSCODE'].str.extract(r'(\d\d\d\d\d\d\d\d\d\d)')
navidata['HSCODE'] = navidata['HSCODE'].astype('int64')

<ipython-input-117-046aa533449b>:4: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will*not* be treated as literal strings when regex=True.
  navidata['HSCODE'] = navidata['HSCODE'].str.replace('.','')


In [118]:
# 6자리로 바꿔주는
def change_six(data):
    df2 = pd.DataFrame(columns=['HSCODE_6'])
    for index in data.index:
        code = str(data['HSCODE'][index])
        HS_code = 0
        if len(str(code)) == 9:
            HS_code = code[0:5]
        elif len(str(code))== 10:
            HS_code = code[0:6]
        else :
            HS_code = ''
        df2 = df2.append({"HSCODE_6":HS_code},ignore_index=True)
    return df2['HSCODE_6']

In [119]:
test_data1['HSCODE_6'] = change_six(test_data1)
navidata['HSCODE_6'] = change_six(navidata)

In [120]:
def preprocessing(text):
    # 개행문자 제거
    text = re.sub('\\\\n', ' ', text)
    # 특수문자 제거
    # 특수문자나 이모티콘 등은 때로는 의미를 갖기도 하지만 여기에서는 제거했습니다.
    # text = re.sub('[?.,;:|\)*~`’!^\-_+<>@\#$%&-=#}※]', '', text)
    # 한글, 영문, 숫자만 남기고 모두 제거하도록 합니다.
    # text = re.sub('[^가-힣ㄱ-ㅎㅏ-ㅣa-zA-Z0-9]', ' ', text)
    # 한글, 영문만 남기고 모두 제거하도록 합니다.
    text = re.sub('[^가-힣ㄱ-ㅎㅏ-ㅣa-zA-Z]', ' ', text)
    return text

In [121]:
for i in range(len(navidata['NM_KO'])):
    sample_content = preprocessing(str(navidata['NM_KO'][i]))
    navidata['NM_KO'][i] = sample_content

<ipython-input-121-a30bc9e6486f>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  navidata['NM_KO'][i] = sample_content


In [122]:
for i in range(len(navidata['NM_EN'])):
    sample_content = preprocessing(str(navidata['NM_EN'][i]))
    navidata['NM_EN'][i] = sample_content

<ipython-input-122-62fe000f8e11>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  navidata['NM_EN'][i] = sample_content


In [215]:
data1 = pd.DataFrame(columns = ['HSCODE', 'HSCODE_6','NM_EN','NM_KO'])
data1['NM_EN'] = test_data1['NM_EN'] + " " + test_data1['KO_add']
data1['NM_KO'] = test_data1['NM_KO'] + " " + test_data1['NM_EN.1']
data1['HSCODE'] = test_data1['HSCODE']
data1['HSCODE_6'] = test_data1['HSCODE_6']

In [216]:
data1 = data1.replace('', np.nan, regex=True)
navidata = navidata.replace('', np.nan, regex=True)
Combination_data = data1.append(navidata)
# 두개 다 결측치인거 없애기  79,154 --> 74,810
Combination_data = Combination_data.replace( np.nan,"-", regex=True)
Conbin_data=Combination_data[(Combination_data['NM_EN'] != '-') |(Combination_data['NM_KO'] != '-')  ]
Conbin_data = Conbin_data.replace("-", np.nan,regex = True)
Combination_data = Combination_data.replace("-", np.nan,regex = True)

In [217]:
Conbin_data

HSCODE HSCODE_6                                              NM_EN  \
1   201300000    20130          Meat of bovine animals Kimlar beef roll     
2   202200000    20220  Edible beef bone with meatfrozen   For food Be...   
3   202200000    20220  Edible beef bone with meatfrozen   For food Be...   
4   202200000    20220  Edible beef bone with meat  Frozen For food Be...   
5   202200000    20220                 Edible beef bone with meatfrozen     
..        ...      ...                                                ...   
66  106901000    10690  Amphibia NEWTS  ETC FROG ORNAMENTAL FROG CYNOP...   
67  106903010    10690  Lug worms LUG WORMS LIVE INVERTEBRATE  SAND TU...   
68  106903020    10690                           Sludge worms EARTHWARMS    
69  106903090    10690  Other OTHER LIVE LEECHES MEDICINAL LEECH LIVE ...   
70  106909000    10690  Other CAENORHABDITIS ELEGANS GALEODES GRANTI R...   

                        NM_KO  
1                     김라 소고기롤  
2     냉동육이 포함된 식용 사골 식품용 사골육   
3     냉동육이 포함된 식용 사골 식품용 사골육   
4     냉동육이 포함된 식용 사골 식품용 사골육   
5               고기를 냉동한 식용 사골  
..                        ...  
66                        양서류  
67                       갯지렁이  
68                       실지렁이  
69                         기타  
70                         기타  

[74810 rows x 4 columns]

In [218]:
print(Conbin_data['NM_EN'].nunique())
print(Conbin_data['NM_KO'].nunique())

33844
12162


In [219]:
Conbin_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 74810 entries, 1 to 70
Data columns (total 4 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   HSCODE    74810 non-null  int64 
 1   HSCODE_6  74810 non-null  object
 2   NM_EN     73760 non-null  object
 3   NM_KO     20168 non-null  object
dtypes: int64(1), object(3)
memory usage: 2.9+ MB


In [220]:
Conbin_data.isnull().sum()

HSCODE          0
HSCODE_6        0
NM_EN        1050
NM_KO       54642
dtype: int64

In [221]:
import nltk
import pickle
from nltk.corpus import stopwords
import re
nltk.download('all')

[nltk_data] Downloading collection 'all'
[nltk_data]    | 
[nltk_data]    | Downloading package abc to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package abc is already up-to-date!
[nltk_data]    | Downloading package alpino to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package alpino is already up-to-date!
[nltk_data]    | Downloading package biocreative_ppi to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package biocreative_ppi is already up-to-date!
[nltk_data]    | Downloading package brown to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package brown is already up-to-date!
[nltk_data]    | Downloading package brown_tei to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data

[nltk_data]    |   Package pl196x is already up-to-date!
[nltk_data]    | Downloading package ppattach to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package ppattach is already up-to-date!
[nltk_data]    | Downloading package problem_reports to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package problem_reports is already up-to-date!
[nltk_data]    | Downloading package propbank to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package propbank is already up-to-date!
[nltk_data]    | Downloading package ptb to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package ptb is already up-to-date!
[nltk_data]    | Downloading package product_reviews_1 to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk

[nltk_data]    |   Package large_grammars is already up-to-date!
[nltk_data]    | Downloading package tagsets to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package tagsets is already up-to-date!
[nltk_data]    | Downloading package snowball_data to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package snowball_data is already up-to-date!
[nltk_data]    | Downloading package bllip_wsj_no_aux to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package bllip_wsj_no_aux is already up-to-date!
[nltk_data]    | Downloading package word2vec_sample to
[nltk_data]    |     C:\Users\DeepLearning_3\AppData\Roaming\nltk_data
[nltk_data]    |     ...
[nltk_data]    |   Package word2vec_sample is already up-to-date!
[nltk_data]    | Downloading package panlex_swadesh to
[nltk_data]    |     C:\Us

True

In [222]:
dictionary = {'신청품':'','또는':'','＊mm':'','  ':' ',"          ":'','품':'',"   ":' ',"    ":' ',"     ":',"      ":' ',"       ":' ',"        ":' ',"         ":' '','제시품':'',' kg ' :''}
Conbin_data.replace(dictionary,regex=True, inplace = True)

In [223]:
Conbin_data['NM_EN']= Conbin_data['NM_EN'].str.lower()      # 모두 소문자로 변경

In [224]:
Conbin_data.to_csv('./data/crawling_data.csv',encoding='utf-8-sig') # 저장할떄

# 토큰화

In [273]:
data = pd.read_csv('./data/crawling_data.csv',encoding='utf-8-sig')

In [274]:
data.reset_index(inplace = True,drop=True)
data.sort_values(by = ['HSCODE'],axis = 0,inplace = True)

In [275]:
data.drop(['Unnamed: 0'],axis = 1, inplace = True)

In [276]:
data_EN = data.copy()
data_KO = data.copy()
data_EN.drop(['NM_KO'],axis = 1, inplace = True)
data_KO.drop(['NM_EN'],axis = 1, inplace = True)
data_EN = data_EN.replace('', np.nan, regex=True)
data_KO = data_KO.replace('', np.nan, regex=True)
data_EN=data_EN.dropna(how='any')
data_KO=data_KO.dropna(how='any')
data_EN.reset_index(inplace = True,drop=True)
data_KO.reset_index(inplace = True, drop = True)

In [277]:
data_EN

HSCODE  HSCODE_6                                              NM_EN
0       101211000     10121  live horses for farm breeding horses purebred ...
1       101219000     10121  live horses horses for purebred breeding anima...
2       101291000     10129  horses for racing horse for racing live horses...
3       101299000     10129  live horses not breeding live horses other hor...
4       101301000     10130                         purebred breeding animals 
...           ...       ...                                                ...
73755  9705000000    970500                                  berlin wall point
73756  9705000000    970500                                  berlin wall point
73757  9705000000    970500                              fossil fossil remains
73758  9705000000    970500   earth guard flashman red flashman filming hel...
73759  9706009000    970600    string instrument violin over a year after p...

[73760 rows x 3 columns]

In [278]:
data_KO

HSCODE  HSCODE_6                  NM_KO
0       101211000     10121                 농가 사육용
1       101219000     10121                     기타
2       101291000     10129                    경주말
3       101299000     10129                     기타
4       101301000     10130                    번식용
...           ...       ...                    ...
20163  3824909090    382490              화학제제 IP  
20164  3824909090    382490           화학약 정전기 방지제 
20165  3824909090    382490           화학약 정전기 방지제 
20166  3824909090    382490   화학 준비물 PHIIV SOMEFC 
20167  3824909090    382490          화학 준비 TZYSB  

[20168 rows x 3 columns]

In [258]:
data_EN[27:]

HSCODE  HSCODE_6                                              NM_EN
27      104209000     10420                                             other 
28      105111000     10511  purebred breeding animals chicks for purebred ...
29      105119000     10511  other day old chicks chicks purebred breeding ...
30      105120000     10512                                           turkeys 
31      105131000     10513  purebred breeding animals dayold ducklings pur...
...           ...       ...                                                ...
73755  9705000000    970500                                  berlin wall point
73756  9705000000    970500                                  berlin wall point
73757  9705000000    970500                              fossil fossil remains
73758  9705000000    970500   earth guard flashman red flashman filming hel...
73759  9706009000    970600    string instrument violin over a year after p...

[73733 rows x 3 columns]

In [261]:
result_df1 = pd.DataFrame(columns=['HSCODE','HSCODE_6','NM_EN'])
for count in range(0,len(data_EN)):
    word_tokens = nltk.word_tokenize(data_EN.loc[count,'NM_EN'])
    tokens_pos  = nltk.pos_tag(word_tokens)
    add_word = ''
    for word , tag in tokens_pos:
        if tag in ['JJ','NN','NNS','VV','VBG','VBN','VBR']:
            if len(word) > 2 :
                add_word += (word + ' ')
    print(add_word)
    result_df1 = result_df1.append({"HSCODE":data_EN.loc[count,"HSCODE"],"HSCODE_6":data_EN.loc[count,"HSCODE_6"],"NM_EN":add_word}, ignore_index=True)
result_df1

live horses farm breeding horses breeding animals farm breeding horse farm breeding live horse horses breeding horse 
live horses horses purebred breeding animals bred breeding horse breeding horse pure breeding animals breeding animals 
horses racing horse racing live horses horse horses horses racing 
live horses breeding live horses other horse live horse horses riding other horses 
purebred breeding animals 
live asses donkey 
live mules other load device dial variable resistor 
milk 
meat fact natural sfn senior cream daeng meo vitalizin marker fact natural sfn junior cream mask pack skin care cosmetic meat fact natural sfn junior cream 
other 
milk 
meat 
other 
purebred breeding animals 
milk 
meat 
other 
purebred breeding animals 
milk 
meat 
other 
purebred breeding animals swines duroc pure breeding pig pure breeding pigs breeding animals 
weighing 
weighing live swine 
purebred breeding animals 
other 
milk goats 
other 
purebred breeding animals chicks purebred breeding fo

patella frozen 
sinew frozen monfort food 
sinew 
foot swine 
foot swine 
meat swin frozen 
meat swin frozen 
tropical fish 
cut bluefin tuna 
cut bluefin tuna 
yellowfin tuna neck meat frozen 
yellowfin tuna neck meat frozen 
yellowfin tunathunnus meat frozen 
frozen yellowfin tuna head 
bigeye tuna cheek meat frozen 
bigeye tunathunnus obesus neck meat frozen 
bluefin tuna meat frozen libya 
bluefin tuna neck meat frozen 
frozen bluefin tuna cheek 
bluefin tuna meat frozen libya 
bluefin tuna neck meat frozen 
frozen bluefin tuna cheek 
cod headfrozen russian frozen cod 
cod headfrozen russian frozen cod 
spp neck meat frozen 
skate nose frozen 
other fishesprotonibea dicanthus 
atlantic bumper frozen frozen lagna senegal 
atlantic bumper frozen frozen lagna senegal 
frozen immature herring roe 
other edible fish offal frozen frozen ling skin 
other edible fish offal frozen frozen ling skin 
other edible fish offal frozen frozen ling tail 
fillet codfrozen 
horn fish fillets 
salmon 

garlic powder 
garlic powder garlic powder 
garlic powder mixed seaweed 
taro stem 
pumpkin 
dried leaves 
dried hemerocallis fulva flowers 
dried vegetable freezedried chives 
carrotdried dried carrot silk slice food carrot glucose 
carrotdried slice food carrot glucose 
carrot 
carrot dried carrot flakes vegetables 
carrot dried carrot flakes vegetables 
carrot 
carrot powder carrot powder 
pumpkin powder pumpkin powder 
pumpkin powder yellowish powder 
cabbagedried slice food cabbage glucose salt 
cabbagedried slice food cabbage glucose salt 
sweet potato simom leaf tea groats potato steam leaf 
squash powder 
squash powder 
dried horseradish flake 
green onion dehydrated green onion 
horseradish powder 
potato dices 
molokheiya dried 
green onion dehydrated green onion 
sweet corn freeze corn 
sweet corn frozen dried sweet corn 
sweet corn frozen dried sweet corn 
sweet corn 
sweet corn 
molokheiya tablets cleanliness 
dried vegetable nopal gel powder 
dried vegetable nopal gel pow

flavoured black tea 
black tea lemon tea 
fermented tea jessie towel 
fermented tea 
oolong tea 
fermented tea sou tsian tea 
assam tea 
jasmine tea 
oolong tea 
oolong tea 
black tea black tea 
tea fermented oolong tea 
tea pearl jasmine tea paper bag food tea jasmine flower 
tea puerh mini tuocha 
teafermented colego tuocha bagsbox tea hgkong 
ooolong tea gbox food tea 
tea 
fermented 
black tea earl grey 
black tea 
black tea 
black tea 
black tea 
black tea 
black tea 
black tea 
tea puerh mini tuocha 
ooolong tea gbox food tea 
black tea joya black tea 
fermented tea jasmine dragon pearl tea 
fermented tea 
fermented tea 
fermented tea 
fermented tea 
fermented tea hwangchagunsan acupuncture 
fermented tea 
black tea tea english breakfast 
black tea tea earl grey srilank 
fermented tea jasmine tea 
fermented tea jasmine dragon pearl tea 
pepper pfeffer schwarz 
pepper fruit hull mixture pepper 
black pepper ground schwarz gemahlen 
seasoning powder food paprika powder corn starch 

corn mealtortilla chip white masa harina 
cereal mealcornoat flour 
corn meal taco 
corn meal taco 
corn meal rasruman available starch 
corn meal polenta 
corn mealmasa 
corn meal maize gritssample 
corn meal 
corn meal corn grits 
corn meal corn grits 
maizecorn meal pregelatinized yellow masa fina 
maizecorn meal pregelatinized yellow masa tortilla chip 
corn meal suntava purple corn snack meal 
corn meal maize gritssample 
rice meal 
oat bran mealorganic oat bran 
meal oats baby cereal oat 
oat meal breakfast preparations bran 
rice meal organic baby cereal rice croatia 
rice meal hmwe myanmar 
glutinous rice meal 
glutinous rice meal 
cauldron nurungji tea 
cauldron nurungji tea 
coicis semen 
oat pellet oat pellet 
oat pellet oat pellet 
oatrolled traditional 
rolled oats 
rolled oats 
rolled oats 
rolled oatsquick oats 
quick oats 
rolled oat raisin oats oat bran 
rolled oats 
oatrolled traditional 
oats oats raw simple bare 
oats oats raw simple bare 
oat moms naturals old oats

...

quilt grace 
cushion stool cvr yellow 
led lighting fitting panel 
led ledrl modules 
led track light type opening ceiling attachment 
coelux 
srl showerhead mounting 
led ledrl modules 
led light panel 
led modules 
light partsteelplate pcb 
light partsteelplate pcb 
led ldval bat ledv registrar 
led lds early balloon 
led jsldw modules 
led jsle early balloon 
led jsle early balloon 
ceiling lightllfml 
led light 
led light panel 
led tube sfl 
led tube sfl 
led high bay light sfd 
led panel lightmaxlight slim 
lighting fixture lsl rmk 
led whcl cap fluorescent spectroscope 
led lsl rmk registrar 
led tube sfl 
led panel lightmaxlight slim 
led flat panel epl 
ceiling lightllfml 
led tube sfl 
led tube light pta 
led factory light pfa 
led factory light pfa 
led light 
lighting fixture lsl rmk 
lighting fixture lsl rmk 
led panel lightmaxlight slim 
led whcl cap fluorescent spectroscope 
led cotton tides 
chandelier republic 
led cotton tides 
decorative rain lamp 
toy block boxtwipe

sink swim brain trainer 
utopia brain trainer 
cross roads brain trainer 
funny farm brain trainer 
hedgehog escape brain trainer 
puzzle toy 
face puzzle 
education toy mom program number fragment puzzle 
pororo parts fruits 
chicken skewer puzzle 
tessellation bird 
tessellation bird 
tangram monthly pack chilgyo nori spring spring touching mathematical phase arc 
tangram monthly pack chilgyo nori spring spring touching mathematical phase arc 
cross roads brain trainer 
kusabi game 
kusabi game 
learning kitchen 
plastic toypororo bowling set 
outfit other toy sets.jesse 
infant tubtime friends 
outfit other toy sets.jesse 
tayo melody ball tentpl 
super click plastic control kit 
fish play plastic pororo fish play toys 
magnetic fishing game 
magnetic fishing game 
bnkr goga battle entry set gouga battle entry 
toysmodel kit haco roommy room set item 
hopping baby rabbit raising 
playing cards personality cards sharero 
playing cards personality cards sharero 
boggle boggle cooks 
b

pinky town diorama pinky street paper diorama diorama 
wooden toys train 
wooden prefabricated dollhouse 
hansel gretel book 
spy penx item 
other toysput outfits 
other toys put sets toys tooling 
other toys put sets toys tooling 
science egg ant set inhalated insect collector ant observation bin 
fish 
barnyard bingo animal farm bingo 
learning train english language sing choochoo presentation number packaging cardarok awards 
animal school house 
pirate box set 
led color matrix mini fan mini fan 
mini buggy xmb 
led color matrix mini fan mini fan 
handy fan cmpropeller shin year enterprise 
vibrating ball pen 
kit imitation gun fabricated toys plastic pistol model 
highway shooter 
model glider paper sheet 
playball toy pvc 
sunglasses rollen sunglasses 
air soft gun 
handgun model toy 
bump bump car model toys 
air soft gun toy 
night sky star stencil kit 
night sky star stencil kit paper stencil constellation night sky 
imitation gun toy toy model pistol 
imitation gun toy toy mo

rebraking boardg 
eva stick 
aluminium nunchakuh 
family pool 
air pool 
strikezon simulator system origin 
carbon fly fishing rods 
fishing rod carbon 
fishing rod carbon 
ptsm fishing rod handle sheet bird mouth 
fishing reels assy lsr fishing reel 
fishing reels spool sla fishing reel 
fishing reels spool sla fishing reel 
fishing sinker fishing rod 
eklsg fishing section guide 
rod repair lotrk 
fishing tackle ayu bags 
rod repair lotrk 
fishing tube 
gocar gokart 
dotto train 
control car boat 
rental kart 
fairground amusement fantasy car 
balloon bust 
kart atvquad bike 
sunshine multi flame systemsm 
rodeo machine 
rodeo machine 
virtual reality simulator nexperience ride 
goblet toss 
motion simulator top drift 
whopper water center 
roll ball 
tub toss 
tub toss 
kart atvquad bike 
whopper water center 
ivory rod 
shell cameo 
sculptured sheath 
sculptured sheath 
other animal caving material articles materials shells handicraft 
motherofpearl shells 
button containing shells

HSCODE HSCODE_6                                              NM_EN
0       101211000    10121  live horses farm breeding horses breeding anim...
1       101219000    10121  live horses horses purebred breeding animals b...
2       101291000    10129  horses racing horse racing live horses horse h...
3       101299000    10129  live horses breeding live horses other horse l...
4       101301000    10130                         purebred breeding animals 
...           ...      ...                                                ...
73755  9705000000   970500                                 berlin wall point 
73756  9705000000   970500                                 berlin wall point 
73757  9705000000   970500                             fossil fossil remains 
73758  9705000000   970500     guard flashman flashman filming helmet outfit 
73759  9706009000   970600          string instrument violin year production 

[73760 rows x 3 columns]

In [262]:
result_df1

HSCODE HSCODE_6                                              NM_EN
0       101211000    10121  live horses farm breeding horses breeding anim...
1       101219000    10121  live horses horses purebred breeding animals b...
2       101291000    10129  horses racing horse racing live horses horse h...
3       101299000    10129  live horses breeding live horses other horse l...
4       101301000    10130                         purebred breeding animals 
...           ...      ...                                                ...
73755  9705000000   970500                                 berlin wall point 
73756  9705000000   970500                                 berlin wall point 
73757  9705000000   970500                             fossil fossil remains 
73758  9705000000   970500     guard flashman flashman filming helmet outfit 
73759  9706009000   970600          string instrument violin year production 

[73760 rows x 3 columns]

In [279]:
for count in data_KO.index:
  #print(count)
  if type(data_KO._get_value(count,'NM_KO')) == str:
    row_s = data_KO._get_value(count,'NM_KO')
    k_str = ''
    add_data = data_KO.iloc[count]
    for c in row_s:
        if ord('가')<= ord(c) <= ord('힣'):
            k_str += c
        else:
            k_str += ' '
    print(r"문장 : {} \n한국어 : {}".format(c,k_str))
    add_data['NM_KO_2'] = k_str
    data_KO = data_KO.append(add_data,ignore_index=True)


문장 : 용 \n한국어 : 농가 사육용
문장 : 타 \n한국어 : 기타
문장 : 말 \n한국어 : 경주말
문장 : 타 \n한국어 : 기타
문장 : 용 \n한국어 : 번식용
문장 : 타 \n한국어 : 기타
문장 :   \n한국어 : 노새 버새 산동물 
문장 : 소 \n한국어 : 젖소
문장 :   \n한국어 : 육우  
문장 : 타 \n한국어 : 기타
문장 : 소 \n한국어 : 젖소
문장 :   \n한국어 : 육우  
문장 : 타 \n한국어 : 기타
문장 :   \n한국어 : 버팔로 번식용 산동물 
문장 : 소 \n한국어 : 젖소
문장 :   \n한국어 : 육우  
문장 : 타 \n한국어 : 기타
문장 : 용 \n한국어 : 번식용
문장 : 소 \n한국어 : 젖소
문장 :   \n한국어 : 육우  
문장 : 타 \n한국어 : 기타
문장 :   \n한국어 : 돼지 번식용 산동물 
문장 :   \n한국어 : 돼지    미만 산동물 
문장 :   \n한국어 : 돼지    이상 산동물 
문장 : 용 \n한국어 : 번식용
문장 : 타 \n한국어 : 기타
문장 : 양 \n한국어 : 젖산양
문장 : 타 \n한국어 : 기타
문장 : 용 \n한국어 : 번식용
문장 : 타 \n한국어 : 기타
문장 :   \n한국어 : 칠면조 산동물 
문장 : 용 \n한국어 : 번식용
문장 : 타 \n한국어 : 기타
문장 :   \n한국어 : 거위 산동물 
문장 :   \n한국어 : 기니아새 산동물 
문장 : 용 \n한국어 : 번식용
문장 : 타 \n한국어 : 기타
문장 : 용 \n한국어 : 번식용
문장 : 타 \n한국어 : 기타
문장 : 조 \n한국어 : 칠면조
문장 : 타 \n한국어 : 기타
문장 :   \n한국어 : 영장류 산동물 
문장 :   \n한국어 : 고래  돌고래류 고래목의 포유동물  바다소 바다소목의 포유동물 
문장 :   \n한국어 : 물개 바다사자와 바다코끼리 기각아목의 포유동물 
문장 :   \n한국어 : 낙타 산동물 
문장 : 용 \n한국어 : 번식용
문장 : 타 \n한국어 :

<ipython-input-279-5c04c4bf5f92>:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  add_data['NM_KO_2'] = k_str
C:\Users\DeepLearning_3\anaconda3\lib\site-packages\pandas\core\indexing.py:692: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value, self.name)


문장 :   \n한국어 : 기타 곤충류 산동물 
문장 : 류 \n한국어 : 양서류
문장 : 이 \n한국어 : 갯지렁이
문장 : 이 \n한국어 : 실지렁이
문장 : 타 \n한국어 : 기타
문장 : 타 \n한국어 : 기타
문장 : 롤 \n한국어 :  김라 소고기롤
문장 :   \n한국어 :  냉동육이 포함된 식용 사골 식용 사골육 
문장 :   \n한국어 :  냉동육이 포함된 식용 사골 식용 사골육 
문장 :   \n한국어 :  냉동육이 포함된 식용 사골 식용 사골육 
문장 : 골 \n한국어 :  고기를 냉동한 식용 사골
문장 : 골 \n한국어 :  고기를 냉동한 식용 사골
문장 : 골 \n한국어 :  고기를 냉동한 식용 사골
문장 :   \n한국어 :  송아지 갈비뼈 냉동 보비 송아지 갈비뼈 
문장 :   \n한국어 :  송아지 갈비뼈 냉동 보비 송아지 갈비뼈 
문장 : 기 \n한국어 :  쇠고기 갈은 냉동 쇠고기
문장 :   \n한국어 :  소냉동 쇠고기 상판 등심 스테이크 소즈박스 쇠고기 육수인산나트륨 소금 양념 올레오진 
문장 : 아 \n한국어 :  햄버거 패티용 냉동 쇠고기 패티 쇠고기 분쇄비프 오스트레일리아
문장 : 기 \n한국어 :  냉동 뼈 없는 소의 고기
문장 : 티 \n한국어 :  쇠고기 간 냉동 햄버거 패티
문장 : 크 \n한국어 :  소고기 첨가 덱스트로스파파 오리지널 노네임 스테이크
문장 : 크 \n한국어 :  쇠고기 첨가 소금 덱스트로스 파파인 워터 샌드위치 스테이크         스테이크
문장 : 크 \n한국어 :  쇠고기 덱스트로스 소금 파파 다진 쇠고기 등심         스테이크
문장 : 크 \n한국어 :  소고기에 소금 덱스트로스 파파인 물에 원래         스테이크
문장 : R \n한국어 :  돼지냉동 칠렐드 뼈 없는 돼지등심 고기 반 토막    
문장 : R \n한국어 :  돼지냉동 칠렐드 뼈 없는 돼지등심 고기 반 토막    
문장 : 음 \n한국어 :  프론트 풋 및 생크 손상 없음
문장 : 뼈 \n한국어 :  목뼈 돼

문장 :   \n한국어 :  굵게 썬 감자 감자 냉동  
문장 :   \n한국어 :  굵게 썬 감자 감자 냉동  
문장 :   \n한국어 :  삶은 감자 냉동 레시피 빠른 탈수 냉동 감자 
문장 : 동 \n한국어 :  감자 냉동
문장 : 컷 \n한국어 :  감자 냉동 탈수 냉동 디너 컷
문장 :   \n한국어 :  완두콩 냉동 녹색 완두콩 
문장 :   \n한국어 :  완두콩 냉동 녹색 완두콩 
문장 :   \n한국어 :  냉동삶은팥 작은 팥을 삶아 얼려라  
문장 :   \n한국어 :  냉동 찐녹두 얼려진 멍콩 
문장 :   \n한국어 :  녹두 냉동 
문장 : N \n한국어 :  냉동 스위트 콘 냉동 익힌 스위트 콘 컷 제아 메이스                          
문장 :   \n한국어 :  스위트 콘 얼린 통곡 슈퍼 스위트 콘 
문장 :   \n한국어 :  스위트콘 얼린           
문장 : 수 \n한국어 :  삶은 옥수수와 냉동 옥수수
문장 : 동 \n한국어 :  스위트옥수수 냉동
문장 :   \n한국어 :  스위트옥수수 냉동 
문장 :   \n한국어 :  스위트옥수수 냉동 
문장 : 수 \n한국어 :  달콤한 옥수수 냉동     냉동 커널 옥수수
문장 : 콘 \n한국어 :  스위트콘 냉동 찐 스위트콘
문장 :   \n한국어 :  마늘 냉동 
문장 :   \n한국어 :  마늘 냉동 마늘 소금 파야자 기름 
문장 :   \n한국어 :  당근 얼린 아기 당근 통째로 
문장 :   \n한국어 :  당근 얼린 아기 당근 통째로 
문장 : 동 \n한국어 :   고추냉동
문장 :   \n한국어 :  무냉채 
문장 :   \n한국어 :  기타 야채 냉동 고수 
문장 :   \n한국어 :  기타 냉동 야채 
문장 : 토 \n한국어 :   토마토 냉동 오븐 반건조 아이큐프 냉동 체리 토마토
문장 : 찜 \n한국어 :  호박 얼린 호박찜
문장 : 토 \n한국어 :   토마토 냉동 오븐 반건조 아이큐프 냉동 체리 토마토
문장 : 물 \n한국어 :  냉

문장 :   \n한국어 :   커피 껍질 및 껍질 껍질 커피 껍질 펠릿 
문장 :   \n한국어 :  커피 껍질 및 피부 
문장 : 질 \n한국어 :  커피 껍질
문장 : 크 \n한국어 :  사료용 커피 껍질 플레이크
문장 : 체 \n한국어 :  버마니아 프렌치 커피 미얀마를 포함한 커피 대체
문장 : 체 \n한국어 :  버마니아 프렌치 커피 미얀마를 포함한 커피 대체
문장 : 만 \n한국어 :  녹차 대만
문장 :   \n한국어 :  녹차 맛차 
문장 : 만 \n한국어 :  녹차 대만
문장 : 스 \n한국어 :  녹차 페체 미뇽 프랑스
문장 : A \n한국어 :  녹차             로잉 티백 박스 녹차       
문장 : 차 \n한국어 :  녹차 녹차
문장 : 차 \n한국어 :  녹차 자스민 녹차
문장 : 차 \n한국어 :  녹차반차
문장 : 차 \n한국어 :  녹차 으깬 녹차
문장 :   \n한국어 :  녹차 아스민 녹차박스 식 녹차자스민 
문장 :   \n한국어 :  피치박스 주입 녹차 녹차 녹차 청어 풀장미각 맛 
문장 : 차 \n한국어 :  녹차
문장 : 차 \n한국어 :  녹차
문장 : 차 \n한국어 :  녹차
문장 : 스 \n한국어 :  녹차 제네사 콰이 프랑스
문장 : 스 \n한국어 :  녹차 플뢰르 드 자스민 프랑스
문장 : 차 \n한국어 :  맛 녹차
문장 : 차 \n한국어 :   그린망고 피치 자스민 그린 발효  얼그레이 블랙 커런트 화이트를 초과하지 않는 즉시 발효된 내용물의 즉시 포장 속 녹차
문장 :   \n한국어 :  녹차 
문장 :   \n한국어 :  녹차 맛                
문장 :   \n한국어 :  녹차 맛                
문장 : 맛 \n한국어 :  녹차 맛
문장 : 차 \n한국어 :  녹차
문장 : 스 \n한국어 :  녹차 제네사 콰이 프랑스
문장 : 차 \n한국어 :  녹차
문장 : 티 \n한국어 :  녹차 쉬니 슈가 로잉 티
문장 : A \n한국어 :  녹차       
문장 : A 

...

문장 : 기 \n한국어 :  스폿 클리너 꺼내기
문장 : 비 \n한국어 :  폐수 처리 준비
문장 : 트 \n한국어 :  타이어 펑크 실란트
문장 : 루 \n한국어 :  튀김가루
문장 : 너 \n한국어 :  연료 인젝터 클리너
문장 : 폭 \n한국어 :  안전 보폭
문장 : 션 \n한국어 :   힌지 솔루션프로세싱 솔루션
문장 : 워 \n한국어 :  바이오 코스모 파워
문장 :   \n한국어 :  화학 준비 중화제 
문장 : 비 \n한국어 :  화학적 준비
문장 : 카 \n한국어 :  콜로이드 실리카
문장 : 스 \n한국어 :  혼합 가스
문장 :   \n한국어 :  자동차 유리 처리 라디칼 코팅 세트  
문장 : 니 \n한국어 :  토양 개선 그라눌라임 미니
문장 : 술 \n한국어 :  토양 개선칼술
문장 :   \n한국어 :  탈취제 탈기된 재료   
문장 : 시 \n한국어 :  모즐 프레시
문장 : 도 \n한국어 :  유니콘 노즐 신선도
문장 : S \n한국어 :  비산포성                        
문장 : 트 \n한국어 :  케미컬 라이트
문장 : 릿 \n한국어 :  페라이트 펠릿
문장 : r \n한국어 :                        
문장 :   \n한국어 :  폐수처리제 액체분해효소  
문장 : 모 \n한국어 :  수분 처리 준비 바이오 코스모
문장 :   \n한국어 :  산소석 미튼 하우스 
문장 : 더 \n한국어 :  주조 공장 몰드 코어     를 위한 준비된 바인더
문장 : 더 \n한국어 :  주조 공장 몰드 코어     를 위한 준비된 바인더
문장 : 더 \n한국어 :  주조 공장 몰드 코어     를 위한 준비된 바인더
문장 : 더 \n한국어 :  주조 공장 몰드 코어     를 위한 준비된 바인더
문장 : 더 \n한국어 :  주조 공장 몰드 코어     를 위한 준비된 바인더
문장 : 더 \n한국어 :  주조 공장 몰드 코어     를 위한 준비된 바인더
문장 : 더 \n한국어 :  주조 공장 몰드 코어 

문장 :   \n한국어 :  금속 도금 준비     무전기 구리     
문장 :   \n한국어 :  금속 도금 준비 수지 부족함  
문장 :   \n한국어 :  금속 도금 준비       메이크업 솔루션  
문장 :   \n한국어 :  금속 도금 준비       보충기  
문장 : C \n한국어 :  금속 도금 준비    
문장 :   \n한국어 :  금속 도금 준비          
문장 :   \n한국어 :  금속 도금 준비물            
문장 : M \n한국어 :  금속 도금 준비    
문장 : M \n한국어 :  금속 도금 준비    
문장 :   \n한국어 :  금속 도금 준비        
문장 :   \n한국어 :  금속 도금 준비          
문장 :   \n한국어 :  염소 처리 파라핀 
문장 :   \n한국어 :  염소 처리 파라핀 
문장 :   \n한국어 :  염소 처리 파라핀 
문장 :   \n한국어 :  염소 처리 파라핀 
문장 :   \n한국어 :  항포밍제            
문장 :   \n한국어 :  안티포밍제           디포아머 
문장 :   \n한국어 :  항포화제 실리콘 용액 노보실 
문장 :   \n한국어 :  항포화제 실리콘 용액 노보실 
문장 :   \n한국어 :  안티포밍 에이전트               
문장 :   \n한국어 :  항포밍제            
문장 : g \n한국어 :            
문장 :   \n한국어 :  소포제  
문장 :   \n한국어 :  항증진제             화합물 
문장 :   \n한국어 :  항포밍제 테고 폼엑스 
문장 :   \n한국어 :  안티포밍제           디포아머 
문장 :   \n한국어 :  안티포밍 에이전트               
문장 :   \n한국어 :  안티포밍 에이전트               
문장 :   \n한국어 :  안티포밍제           디포아머 
문장 :   \n한국어 :  안티포밍제    

문장 :   \n한국어 :  화학제제   티모신  
문장 :   \n한국어 :  화학 조제의 날    복합체 
문장 :   \n한국어 :  화학 물질 준비      
문장 : H \n한국어 :  막대 조명 막대    
문장 :   \n한국어 :  윤기고 화학제제  
문장 :   \n한국어 :  코팅제 모노랄용 화학제 첨가제 
문장 :   \n한국어 :  화학제제 그라눌레 험산  
문장 :   \n한국어 :  화학제제 그라눌레 험산  
문장 :   \n한국어 :  옥수수 전분 제제 에코 쿠션       
문장 :   \n한국어 :  옥수수 전분 제제 에코 쿠션       
문장 :   \n한국어 :  옥시피아 소나무  
문장 :   \n한국어 :  수소화 말티톨 시럽          
문장 :   \n한국어 :  수소화 말티톨 시럽          
문장 : 제 \n한국어 :  실리콘이 함유된 화학 제
문장 :   \n한국어 :  화학약       
문장 :   \n한국어 :  화학약       
문장 : E \n한국어 :  화학물질 준비 컨테이너                 
문장 : E \n한국어 :  화학물질 준비 컨테이너                 
문장 :   \n한국어 :  화학제제 
문장 :   \n한국어 :  화학제제 
문장 :   \n한국어 :  화학 준비      
문장 : K \n한국어 :  화학제제               
문장 :   \n한국어 :  화학약 과탄산나트륨 코팅 
문장 :   \n한국어 :  화학제제      
문장 :   \n한국어 :  이중 시트      
문장 :   \n한국어 :  화학제제      
문장 :   \n한국어 :  화학 준비         
문장 :   \n한국어 :  콜드 팩     싱글 콜드 팩 
문장 :   \n한국어 :  콜드 팩     싱글 콜드 팩 
문장 : 물 \n한국어 :  화학 제제 캐비어 추출물
문장 : 제 \n한국어 :  화학제제
문장 :   \n한국어 :  화학약 습기   
문장 

문장 :   \n한국어 :  주제 화학약 스틱 방지 그래피티 코팅제          
문장 :   \n한국어 :  화학제제 
문장 :   \n한국어 :  화학 조제 천연    
문장 :   \n한국어 :  화학 준비             
문장 :   \n한국어 :  화학약        캐리어    
문장 :   \n한국어 :  화학약        캐리어    
문장 :   \n한국어 :  화학 준비물        
문장 :   \n한국어 :  화학약        캐리어    
문장 :   \n한국어 :  화학 준비 건조제 봉투 
문장 :   \n한국어 :  화학 준비 건조제 봉투 
문장 :   \n한국어 :  화학약       
문장 :   \n한국어 :  화학약       
문장 :   \n한국어 :  화학 제제 우유 단백질 추출액 
문장 :   \n한국어 :  화학 조제한    하이드로 세라미드  
문장 :   \n한국어 :  화학 조제한    하이드로 세라미드  
문장 :   \n한국어 :  화학 준비     
문장 :   \n한국어 :  화학 제제 표면 처리                       
문장 :   \n한국어 :  화학 제제 에폭시 반응 희석제 카르돌렌시 
문장 :   \n한국어 :  화학 준비       
문장 : B \n한국어 :  화학 준비     
문장 :   \n한국어 :  화학 제제 알루미나 지르코니아 그레인     
문장 :   \n한국어 :  화학 제제 코팅 흑연 글루탐산 일나트륨 
문장 :   \n한국어 :  화학 제제 코팅 흑연 글루탐산 일나트륨 
문장 :   \n한국어 :  페인트첨가제 화학제제         
문장 :   \n한국어 :  페인트첨가제 화학제제         
문장 :   \n한국어 :  페인트첨가제 화학제제         
문장 :   \n한국어 :  화학비율         
문장 :   \n한국어 :  화학제제           
문장 :   \n한국어 :  화학제제           
문장 :   

문장 :   \n한국어 :  화학 제제     
문장 :   \n한국어 :  화학약 초미세 이산화 티타늄     
문장 :   \n한국어 :  화학약 초미세 이산화 티타늄     
문장 :   \n한국어 :  화학 준비        복합체 
문장 : R \n한국어 :  화학제제                   미립자 오일 컨디셔너   
문장 :   \n한국어 :  화학제제     
문장 :   \n한국어 :  화학제제     
문장 :   \n한국어 :  화학 조영제                      
문장 :   \n한국어 :  화학제제 
문장 :   \n한국어 :  화학 제제 표면 처리                       
문장 :   \n한국어 :  화학 조제 천연    
문장 :   \n한국어 :  화학 준비             
문장 :   \n한국어 :  화학약        캐리어    
문장 :   \n한국어 :  화학약        캐리어    
문장 :   \n한국어 :  골든입상배양토 배지 배지 배지 심기  
문장 :   \n한국어 :  화학 준비물        
문장 :   \n한국어 :  화학 준비 건조제 봉투 
문장 :   \n한국어 :  화학 준비 건조제 봉투 
문장 :   \n한국어 :  화학약       
문장 :   \n한국어 :  화학약       
문장 :   \n한국어 :  화학 제제 우유 단백질 추출액 
문장 :   \n한국어 :  화학 조제한    하이드로 세라미드  
문장 :   \n한국어 :  화학 조제한    하이드로 세라미드  
문장 :   \n한국어 :  화학 준비     
문장 :   \n한국어 :  캘비 파워 화학 준비물       전력  
문장 :   \n한국어 :  화학 준비물 실리콘 갭 패드 
문장 :   \n한국어 :  화학 준비물                중간체 
문장 :   \n한국어 :  기타 준비      
문장 :   \n한국어 :  기타 준비      
문장 :   \n한국어 : 

In [284]:
data_KO=data_KO[20168:]

In [291]:
data_KO.drop(['NM_KO'],axis = 1, inplace = True)
data_KO.rename(columns = {'NM_KO_2':'NM_KO'}, inplace = True)

C:\Users\DeepLearning_3\anaconda3\lib\site-packages\pandas\core\frame.py:4308: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(
C:\Users\DeepLearning_3\anaconda3\lib\site-packages\pandas\core\frame.py:4441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().rename(
